### Segmenting & Clustering Neighborhoods in Toronto (Assignment: Week3)

###### Question 1

In [1]:
# We begin by importing pandas library for data analysis
import pandas as pd

# we proceed to scrap wikipedia page: 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M' 
# in order to obtain the data that is in the table of postal codes & transform data in a new pandas dataframe
df = pd.read_html('https://en.wikipedia.org/w/index.php?title=List_of_postal_codes_of_Canada:_M')[0]

# we drop any Boroughs with value 'Not assigned'
df = df[df.Borough!='Not assigned']

In [2]:
# we check dataframe columns
df.columns
# Our dataframe contains columns 'Postal Code', 'Borough' & 'Neighbourhood'.

Index(['Postal Code', 'Borough', 'Neighbourhood'], dtype='object')

In [3]:
# let's view first 10 rows
df.head(10)
# We observe that more than one neighborhood can exist in one postal code area

Postal Code           Borough                                Neighbourhood
2          M3A        North York                                    Parkwoods
3          M4A        North York                             Victoria Village
4          M5A  Downtown Toronto                    Regent Park, Harbourfront
5          M6A        North York             Lawrence Manor, Lawrence Heights
6          M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government
8          M9A         Etobicoke      Islington Avenue, Humber Valley Village
9          M1B       Scarborough                               Malvern, Rouge
11         M3B        North York                                    Don Mills
12         M4B         East York              Parkview Hill, Woodbine Gardens
13         M5B  Downtown Toronto                     Garden District, Ryerson

In [6]:
df.groupby(df['Neighbourhood']=='Not Assigned').count()
# we make sure that there are no Neighbourhoods with value 'Not Assigned'

Postal Code  Borough  Neighbourhood
Neighbourhood                                     
False                  103      103            103

In [7]:
print('Number of rows in our dataframe is', df.shape[0]) 

Number of rows in our dataframe is 103


##### Question 2

In [8]:
# we proceed by getting the latitude and the longitude coordinates of each neighborhood
df_geo = pd.read_csv("https://cocl.us/Geospatial_data")
# we merge the dataframes 
new_df = pd.merge(df, df_geo)
new_df.head()

Postal Code           Borough                                Neighbourhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

##### Question 3

In [10]:
import numpy as np # library to handle data in a vectorized manner

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: ...working... done

## Package Plan ##

  environment location: C:\Users\Apostolos\anaconda3

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    conda-4.9.2                |   py38haa244fe_0         3.1 MB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    geopy-2.0.0                |     pyh9f0ad1d_0          63 KB  conda-forge
    python_abi-3.8             |           1_cp38           4 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.2 MB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.50-py_0
  geopy              conda-forge/noarch::geopy-2.0.0-pyh9f0ad1d_0
  python_abi         conda-forge/win-64::python_abi-3.8-1_cp38

The following pac

In [12]:
# get location of Toronto using geopy
address = 'Toronto'

geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [14]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(new_df['Latitude'], new_df['Longitude'], new_df['Borough'], new_df['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

##### Define Foursquare Credentials and Version

In [15]:
CLIENT_ID = 'ESPT1Q0S12HZNN0Q0TXZKJKZAOOFAYOQXRVKXPRLRGM1D1E5' # my Foursquare ID
CLIENT_SECRET = 'GBDB1OTGR5FDLAIDC41VUXZ115GU13COU0CPDONYU2JUCOH5' # my Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('My credentials:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

My credentials:
CLIENT_ID: ESPT1Q0S12HZNN0Q0TXZKJKZAOOFAYOQXRVKXPRLRGM1D1E5
CLIENT_SECRET:GBDB1OTGR5FDLAIDC41VUXZ115GU13COU0CPDONYU2JUCOH5


#### Get the top 100 venues that are in Toronto within a radius of 1000 meters

In [16]:
def getNearbyVenues(names, latitudes, longitudes, radius=1000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [18]:
# run the function above to each neighborhood and create a new dataframe called toronto_venues
toronto_venues = getNearbyVenues(names=new_df['Neighbourhood'],
                                 latitudes=new_df['Latitude'],
                                 longitudes=new_df['Longitude'])

toronto_venues

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue, Humber Valley Village
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto, Broadview North (Old East York)
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmo

Neighbourhood  \
0                                             Parkwoods   
1                                             Parkwoods   
2                                             Parkwoods   
3                                             Parkwoods   
4                                             Parkwoods   
5                                             Parkwoods   
6                                             Parkwoods   
7                                             Parkwoods   
8                                             Parkwoods   
9                                             Parkwoods   
10                                            Parkwoods   
11                                            Parkwoods   
12                                            Parkwoods   
13                                            Parkwoods   
14                                            Parkwoods   
15                                            Parkwoods   
16                                            Parkwoods   
17                                            Parkwoods   
18                                            Parkwoods   
19                                            Parkwoods   
20                                            Parkwoods   
21                                            Parkwoods   
22                                            Parkwoods   
23                                            Parkwoods   
24                                            Parkwoods   
25                                            Parkwoods   
26                                            Parkwoods   
27                                            Parkwoods   
28                                     Victoria Village   
29                                     Victoria Village   
30                                     Victoria Village   
31                                     Victoria Village   
32                                     Victoria Village   
33                                     Victoria Village   
34                                     Victoria Village   
35                                     Victoria Village   
36                                     Victoria Village   
37                                     Victoria Village   
38                                     Victoria Village   
39                                     Victoria Village   
40                                     Victoria Village   
41                                     Victoria Village   
42                            Regent Park, Harbourfront   
43                            Regent Park, Harbourfront   
44                            Regent Park, Harbourfront   
45                            Regent Park, Harbourfront   
46                            Regent Park, Harbourfront   
47                            Regent Park, Harbourfront   
48                            Regent Park, Harbourfront   
49                            Regent Park, Harbourfront   
50                            Regent Park, Harbourfront   
51                            Regent Park, Harbourfront   
52                            Regent Park, Harbourfront   
53                            Regent Park, Harbourfront   
54                            Regent Park, Harbourfront   
55                            Regent Park, Harbourfront   
56                            Regent Park, Harbourfront   
57                            Regent Park, Harbourfront   
58                            Regent Park, Harbourfront   
59                            Regent Park, Harbourfront   
60                            Regent Park, Harbourfront   
61                            Regent Park, Harbourfront   
62                            Regent Park, Harbourfront   
63                            Regent Park, Harbourfront   
64                            Regent Park, Harbourfront   
65                            Regent Park, Harbourfront   
66                            Regent Park, Harbourfront   
67                            

In [19]:
# check size of resulting dataframe
print(toronto_venues.shape)
toronto_venues.head()

(4879, 7)


Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0     Parkwoods               43.753259               -79.329656   
1     Parkwoods               43.753259               -79.329656   
2     Parkwoods               43.753259               -79.329656   
3     Parkwoods               43.753259               -79.329656   
4     Parkwoods               43.753259               -79.329656   

                Venue  Venue Latitude  Venue Longitude        Venue Category  
0     Allwyn's Bakery       43.759840       -79.324719  Caribbean Restaurant  
1         Tim Hortons       43.760668       -79.326368                  Café  
2     Brookbanks Park       43.751976       -79.332140                  Park  
3   Bruno's valu-mart       43.746143       -79.324630         Grocery Store  
4  Shoppers Drug Mart       43.760857       -79.324961              Pharmacy

In [21]:
# let's check how many venues were returned for each neighborhood
toronto_venues.groupby('Neighbourhood').count()

Neighbourhood Latitude  \
Neighbourhood                                                                
Agincourt                                                               51   
Alderwood, Long Branch                                                  24   
Bathurst Manor, Wilson Heights, Downsview North                         29   
Bayview Village                                                         14   
Bedford Park, Lawrence Manor East                                       39   
Berczy Park                                                            100   
Birch Cliff, Cliffside West                                             15   
Brockton, Parkdale Village, Exhibition Place                           100   
Business reply mail Processing Centre, South Ce...                      50   
CN Tower, King and Spadina, Railway Lands, Harb...                      14   
Caledonia-Fairbanks                                                     22   
Canada Post Gateway Processing Centre                                   53   
Cedarbrae                                                               29   
Central Bay Street                                                     100   
Christie                                                               100   
Church and Wellesley                                                   100   
Clarks Corners, Tam O'Shanter, Sullivan                                 39   
Cliffside, Cliffcrest, Scarborough Village West                         11   
Commerce Court, Victoria Hotel                                         100   
Davisville                                                             100   
Davisville North                                                       100   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        16   
Don Mills                                                               75   
Dorset Park, Wexford Heights, Scarborough Town ...                      42   
Downsview                                                               67   
Dufferin, Dovercourt Village                                            64   
East Toronto, Broadview North (Old East York)                           98   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      16   
Fairview, Henry Farm, Oriole                                            44   
First Canadian Place, Underground city                                 100   
Forest Hill North & West, Forest Hill Road Park                         49   
Garden District, Ryerson                                               100   
Glencairn                                                               35   
Golden Mile, Clairlea, Oakridge                                         28   
Guildwood, Morningside, West Hill                                       24   
Harbourfront East, Union Station, Toronto Islands                      100   
High Park, The Junction South                                          100   
Hillcrest Village                                                       21   
Humber Summit                                                           10   
Humberlea, Emery                                                         8   
Humewood-Cedarvale                                                      27   
India Bazaar, The Beaches West                                          76   
Islington Avenue, Humber Valley Village                                 12   
Kennedy Park, Ionview, East Birchmount Park                             28   
Kensington Market, Chinatown, Grange Park                              100   
Kingsview Village, St. Phillips, Martin Grove G...                      15   
Lawrence Manor, Lawrence Heights                                        44   
Lawrence Park                                                            8   
Leaside                                                                 60   
Little Portugal, Trinity                                               100

In [23]:
# Let's find out how many unique categories can be curated from all the returned venues
print('There are {} unique categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 335 unique categories.


#### Neighbourhood Analysis

In [24]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighbourhood column back to dataframe
toronto_onehot['Neighbourhood'] = toronto_venues['Neighbourhood'] 

# move neighbourhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighbourhood  Accessories Store  Afghan Restaurant  African Restaurant  \
0     Parkwoods                  0                  0                   0   
1     Parkwoods                  0                  0                   0   
2     Parkwoods                  0                  0                   0   
3     Parkwoods                  0                  0                   0   
4     Parkwoods                  0                  0                   0   

   Airport  American Restaurant  Amphitheater  Animal Shelter  Antique Shop  \
0        0                    0             0               0             0   
1        0                    0             0               0             0   
2        0                    0             0               0             0   
3        0                    0             0               0             0   
4        0                    0             0               0             0   

   Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0         0            0           0                    0                 0   
1         0            0           0                    0                 0   
2         0            0           0                    0                 0   
3         0            0           0                    0                 0   
4         0            0           0                    0                 0   

   Athletics & Sports  Auto Dealership  Auto Workshop  Automotive Shop  \
0                   0                0              0                0   
1                   0                0              0                0   
2                   0                0              0                0   
3                   0                0              0                0   
4                   0                0              0                0   

   BBQ Joint  Baby Store  Badminton Court  Bagel Shop  Bakery  Bank  Bar  \
0          0           0                0           0       0     0    0   
1          0           0                0           0       0     0    0   
2          0           0                0           0       0     0    0   
3          0           0                0           0       0     0    0   
4          0           0                0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Stadium  Beach  Beach Bar  \
0               0                 0                   0      0          0   
1               0                 0                   0      0          0   
2               0                 0                   0      0          0   
3               0                 0                   0      0          0   
4               0                 0                   0      0          0   

   Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  Bistro  Bookstore  \
0         0           0                   0          0       0          0   
1         0           0                   0          0       0          0   
2         0           0                   0          0       0          0   
3         0           0                   0          0       0          0   
4         0           0                   0          0       0          0   

   Botanical Garden  Boutique  Bowling Alley  Boxing Gym  \
0                 0         0              0           0   
1                 0         0              0           0   
2                 0         0              0           0   
3                 0         0              0           0   
4                 0         0              0           0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  Bridge  \
0                     0               0        0            0       0   
1                     0               0        0            0       0   
2                     0               0        0            0       0   
3                     0               0        0            0       0   
4                     0            

In [25]:
# check dataframe size
toronto_onehot.shape

(4879, 336)

In [26]:
# let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_grouped.head

Neighbourhood  Accessories Store  \
0                                           Agincourt           0.000000   
1                              Alderwood, Long Branch           0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North           0.000000   
3                                     Bayview Village           0.000000   
4                   Bedford Park, Lawrence Manor East           0.000000   
5                                         Berczy Park           0.000000   
6                         Birch Cliff, Cliffside West           0.000000   
7        Brockton, Parkdale Village, Exhibition Place           0.010000   
8   Business reply mail Processing Centre, South C...           0.000000   
9   CN Tower, King and Spadina, Railway Lands, Har...           0.000000   
10                                Caledonia-Fairbanks           0.000000   
11              Canada Post Gateway Processing Centre           0.000000   
12                                          Cedarbrae           0.000000   
13                                 Central Bay Street           0.000000   
14                                           Christie           0.000000   
15                               Church and Wellesley           0.000000   
16            Clarks Corners, Tam O'Shanter, Sullivan           0.000000   
17    Cliffside, Cliffcrest, Scarborough Village West           0.000000   
18                     Commerce Court, Victoria Hotel           0.000000   
19                                         Davisville           0.000000   
20                                   Davisville North           0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn           0.000000   
22                                          Don Mills           0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...           0.023810   
24                                          Downsview           0.000000   
25                       Dufferin, Dovercourt Village           0.000000   
26      East Toronto, Broadview North (Old East York)           0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...           0.000000   
28                       Fairview, Henry Farm, Oriole           0.000000   
29             First Canadian Place, Underground city           0.000000   
30    Forest Hill North & West, Forest Hill Road Park           0.000000   
31                           Garden District, Ryerson           0.000000   
32                                          Glencairn           0.000000   
33                    Golden Mile, Clairlea, Oakridge           0.000000   
34                  Guildwood, Morningside, West Hill           0.000000   
35  Harbourfront East, Union Station, Toronto Islands           0.000000   
36                      High Park, The Junction South           0.000000   
37                                  Hillcrest Village           0.000000   
38                                      Humber Summit           0.000000   
39                                   Humberlea, Emery           0.000000   
40                                 Humewood-Cedarvale           0.000000   
41                     India Bazaar, The Beaches West           0.000000   
42            Islington Avenue, Humber Valley Village           0.000000   
43        Kennedy Park, Ionview, East Birchmount Park           0.000000   
44          Kensington Market, Chinatown, Grange Park           0.000000   
45  Kingsview Village, St. Phillips, Martin Grove ...           0.000000   
46                   Lawrence Manor, Lawrence Heights           0.022727   
47                                      Lawrence Park           0.000000   
48                                            Leaside           0.000000   
49                           Little Portugal, Trinity           0.000000   
50                                     Malvern, Rouge           0.000000   
51  Milliken, Agincourt North, Steeles East, L'Amo...           0.000000   
52  Mimico N

In [27]:
# check dataframe size
toronto_grouped.shape

(98, 336)

In [29]:
# Let's print each neighborhood along with the top 5 most common venues
num_top_venues = 5

for hood in toronto_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agincourt----
                  venue  freq
0    Chinese Restaurant  0.14
1         Shopping Mall  0.06
2  Caribbean Restaurant  0.04
3                Bakery  0.04
4           Coffee Shop  0.04


----Alderwood, Long Branch----
               venue  freq
0     Discount Store  0.12
1        Pizza Place  0.08
2           Pharmacy  0.08
3  Convenience Store  0.08
4                Pub  0.04


----Bathurst Manor, Wilson Heights, Downsview North----
                       venue  freq
0                       Bank  0.07
1                Coffee Shop  0.07
2                   Ski Area  0.03
3  Middle Eastern Restaurant  0.03
4          Mobile Phone Shop  0.03


----Bayview Village----
                 venue  freq
0  Japanese Restaurant  0.14
1                 Bank  0.14
2          Gas Station  0.14
3        Grocery Store  0.14
4                 Park  0.07


----Bedford Park, Lawrence Manor East----
                venue  freq
0  Italian Restaurant  0.08
1         Coffee Shop  0.08
2      Sand

4                  Park  0.06


----St. James Town----
         venue  freq
0  Coffee Shop  0.10
1         Café  0.08
2   Restaurant  0.06
3    Gastropub  0.04
4        Hotel  0.03


----St. James Town, Cabbagetown----
                 venue  freq
0                Diner  0.06
1                 Café  0.06
2  Japanese Restaurant  0.06
3            Gastropub  0.06
4                 Park  0.06


----Steeles West, L'Amoreaux West----
                  venue  freq
0    Chinese Restaurant  0.14
1           Pizza Place  0.07
2           Coffee Shop  0.07
3          Intersection  0.07
4  Fast Food Restaurant  0.07


----Stn A PO Boxes----
                 venue  freq
0          Coffee Shop  0.12
1                 Café  0.07
2                Hotel  0.05
3           Restaurant  0.05
4  Japanese Restaurant  0.05


----Studio District----
                 venue  freq
0          Coffee Shop  0.07
1                  Bar  0.05
2  American Restaurant  0.05
3              Brewery  0.05
4                

In [90]:
# Let's put that into a pandas dataframe
# we create a function to sort the venues in descending order.

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

# we create the new dataframe and display the top 10 venues for each neighborhood

num_top_venues = 10
indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighbourhoods_venues_sorted = pd.DataFrame(columns=columns)
neighbourhoods_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighbourhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighbourhoods_venues_sorted

Neighbourhood   1st Most Common Venue  \
0                                           Agincourt      Chinese Restaurant   
1                              Alderwood, Long Branch          Discount Store   
2     Bathurst Manor, Wilson Heights, Downsview North             Coffee Shop   
3                                     Bayview Village           Grocery Store   
4                   Bedford Park, Lawrence Manor East      Italian Restaurant   
5                                         Berczy Park             Coffee Shop   
6                         Birch Cliff, Cliffside West                    Park   
7        Brockton, Parkdale Village, Exhibition Place             Coffee Shop   
8   Business reply mail Processing Centre, South C...                    Park   
9   CN Tower, King and Spadina, Railway Lands, Har...             Coffee Shop   
10                                Caledonia-Fairbanks                Pharmacy   
11              Canada Post Gateway Processing Centre             Coffee Shop   
12                                          Cedarbrae             Coffee Shop   
13                                 Central Bay Street             Coffee Shop   
14                                           Christie       Korean Restaurant   
15                               Church and Wellesley             Coffee Shop   
16            Clarks Corners, Tam O'Shanter, Sullivan             Coffee Shop   
17    Cliffside, Cliffcrest, Scarborough Village West             Pizza Place   
18                     Commerce Court, Victoria Hotel             Coffee Shop   
19                                         Davisville             Coffee Shop   
20                                   Davisville North             Coffee Shop   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn  Furniture / Home Store   
22                                          Don Mills              Restaurant   
23  Dorset Park, Wexford Heights, Scarborough Town...              Restaurant   
24                                          Downsview             Coffee Shop   
25                       Dufferin, Dovercourt Village                    Café   
26      East Toronto, Broadview North (Old East York)                    Café   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...             Coffee Shop   
28                       Fairview, Henry Farm, Oriole             Coffee Shop   
29             First Canadian Place, Underground city             Coffee Shop   
30    Forest Hill North & West, Forest Hill Road Park                    Park   
31                           Garden District, Ryerson             Coffee Shop   
32                                          Glencairn           Grocery Store   
33                    Golden Mile, Clairlea, Oakridge                Bus Line   
34                  Guildwood, Morningside, West Hill             Pizza Place   
35  Harbourfront East, Union Station, Toronto Islands             Coffee Shop   
36                      High Park, The Junction South                    Café   
37                                  Hillcrest Village                Pharmacy   
38                                      Humber Summit       Electronics Store   
39                                   Humberlea, Emery                  Bakery   
40                                 Humewood-Cedarvale             Pizza Place   
41                     India Bazaar, The Beaches West       Indian Restaurant   
42            Islington Avenue, Humber Valley Village                Pharmacy   
43        Kennedy Park, Ionview, East Birchmount Park             Coffee Shop   
44          Kensington Market, Chinatown, Grange Park                    Café   
45  Kingsview Village, St. Phillips, Martin Grove ...                Pharmacy   
46                   Lawrence Manor, Lawrence Heights          Clothing Store   
47                                      Lawrence Park                    Park   
48                                            Leaside             Coffe

#### Clustering Neighbourhoods 

In [91]:
# Run k-means to cluster the neighborhood into 5 clusters
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighbourhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 3, 3, 2, 2, 2, 0, 2, 2, 2])

In [92]:
# Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
# add clustering labels
neighbourhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = new_df

# merge toronto_grouped with new_df to add latitude/longitude for each neighbourhood
toronto_merged = toronto_merged.join(neighbourhoods_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')
toronto_merged = toronto_merged.dropna()
toronto_merged = toronto_merged.astype({"Cluster Labels": int})
toronto_merged.head()

Postal Code           Borough                                Neighbourhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
0  43.753259 -79.329656               3                  Park   
1  43.725882 -79.315572               2           Coffee Shop   
2  43.654260 -79.360636               2           Coffee Shop   
3  43.718518 -79.464763               2        Clothing Store   
4  43.662301 -79.389494               2           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
0     Convenience Store         Shopping Mall               Bus Stop   
1  Gym / Fitness Center           Men's Store  Portuguese Restaurant   
2                   Pub               Theater                   Park   
3  Fast Food Restaurant           Coffee Shop             Restaurant   
4                  Park      Sushi Restaurant    Japanese Restaurant   

  5th Most Common Venue 6th Most Common Venue  7th Most Common Venue  \
0              Pharmacy  Fast Food Restaurant         Shop & Service   
1   Sporting Goods Shop           Golf Course           Intersection   
2                  Café        Breakfast Spot                 Bakery   
3   Fried Chicken Joint          Dessert Shop  Vietnamese Restaurant   
4    Italian Restaurant                  Café                  Diner   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0            Tennis Court  Caribbean Restaurant            Supermarket  
1       French Restaurant          Hockey Arena             Playground  
2                   Diner            Restaurant  Performing Arts Venue  
3  Furniture / Home Store      Sushi Restaurant      Accessories Store  
4            Dance Studio        Cosmetics Shop         Breakfast Spot

In [93]:
# Finally, let's visualize the resulting clusters
# create map
import matplotlib.cm as cm
import matplotlib.colors as colors

map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [103]:
# Cluster 1
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0]

Postal Code      Borough  \
11         M9B    Etobicoke   
12         M1C  Scarborough   
22         M1G  Scarborough   
57         M9M   North York   
58         M1N  Scarborough   
66         M2P   North York   

                                        Neighbourhood   Latitude  Longitude  \
11  West Deane Park, Princess Gardens, Martin Grov...  43.650943 -79.554724   
12             Rouge Hill, Port Union, Highland Creek  43.784535 -79.160497   
22                                             Woburn  43.770992 -79.216917   
57                                   Humberlea, Emery  43.724766 -79.532242   
58                        Birch Cliff, Cliffside West  43.692657 -79.264848   
66                                    York Mills West  43.752758 -79.400049   

    Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
11               0                  Park           Pizza Place   
12               0                  Park        Breakfast Spot   
22               0                  Park           Coffee Shop   
57               0                Bakery      Storage Facility   
58               0                  Park     Convenience Store   
66               0                  Park            Restaurant   

   3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
11            Restaurant                  Bank          Grocery Store   
12          Burger Joint    Italian Restaurant             Playground   
22     Mobile Phone Shop  Fast Food Restaurant     Chinese Restaurant   
57           Golf Course         Auto Workshop         Discount Store   
58                 Diner       Thai Restaurant  General Entertainment   
66           Coffee Shop           Gas Station          Grocery Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
11                   Gym    Mexican Restaurant        Clothing Store   
12       Fireworks Store           Event Space    Falafel Restaurant   
22     Indian Restaurant          Dessert Shop           Event Space   
57           Gas Station                  Park     Convenience Store   
58                   Gym              Gym Pool          Skating Rink   
66                   Gym             Pet Store         Bowling Alley   

   9th Most Common Venue 10th Most Common Venue  
11     Fish & Chips Shop                  Hotel  
12                  Farm         Farmers Market  
22                  Farm         Farmers Market  
57                  Food   Ethiopian Restaurant  
58         Auto Workshop        College Stadium  
66               Dog Run             Playground

In [104]:
# Cluster 2
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1]

Postal Code    Borough                        Neighbourhood   Latitude  \
94         M9W  Etobicoke  Northwest, West Humber - Clairville  43.706748   

    Longitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
94 -79.594054               1                Lounge           Coffee Shop   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
94   Filipino Restaurant  Ethiopian Restaurant           Event Space   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
94    Falafel Restaurant                  Farm        Farmers Market   

   9th Most Common Venue 10th Most Common Venue  
94  Fast Food Restaurant                  Field

In [105]:
# Cluster 3
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2]

Postal Code           Borough  \
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
6           M1B       Scarborough   
7           M3B        North York   
9           M5B  Downtown Toronto   
13          M3C        North York   
14          M4C         East York   
15          M5C  Downtown Toronto   
19          M4E      East Toronto   
20          M5E  Downtown Toronto   
23          M4G         East York   
24          M5G  Downtown Toronto   
25          M6G  Downtown Toronto   
29          M4H         East York   
30          M5H  Downtown Toronto   
31          M6H      West Toronto   
33          M2J        North York   
34          M3J        North York   
35          M4J         East York   
36          M5J  Downtown Toronto   
37          M6J      West Toronto   
39          M2K        North York   
41          M4K      East Toronto   
42          M5K  Downtown Toronto   
43          M6K      West Toronto   
47          M4L      East Toronto   
48          M5L  Downtown Toronto   
52          M2M        North York   
54          M4M      East Toronto   
55          M5M        North York   
56          M6M              York   
59          M2N        North York   
61          M4N   Central Toronto   
62          M5N   Central Toronto   
65          M1P       Scarborough   
67          M4P   Central Toronto   
68          M5P   Central Toronto   
69          M6P      West Toronto   
73          M4R   Central Toronto   
74          M5R   Central Toronto   
75          M6R      West Toronto   
76          M7R       Mississauga   
79          M4S   Central Toronto   
80          M5S  Downtown Toronto   
81          M6S      West Toronto   
83          M4T   Central Toronto   
84          M5T  Downtown Toronto   
86          M4V   Central Toronto   
87          M5V  Downtown Toronto   
88          M8V         Etobicoke   
91          M4W  Downtown Toronto   
92          M5W  Downtown Toronto   
96          M4X  Downtown Toronto   
97          M5X  Downtown Toronto   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
102         M8Z         Etobicoke   

                                         Neighbourhood   Latitude  Longitude  \
1                                     Victoria Village  43.725882 -79.315572   
2                            Regent Park, Harbourfront  43.654260 -79.360636   
3                     Lawrence Manor, Lawrence Heights  43.718518 -79.464763   
4          Queen's Park, Ontario Provincial Government  43.662301 -79.389494   
6                                       Malvern, Rouge  43.806686 -79.194353   
7                                            Don Mills  43.745906 -79.352188   
9                             Garden District, Ryerson  43.657162 -79.378937   
13                                           Don Mills  43.725900 -79.340923   
14                                    Woodbine Heights  43.695344 -79.318389   
15                                      St. James Town  43.651494 -79.375418   
19                                         The Beaches  43.676357 -79.293031   
20                                         Berczy Park  43.644771 -79.373306   
23                                             Leaside  43.709060 -79.363452   
24                                  Central Bay Street  43.657952 -79.387383   
25                                            Christie  43.669542 -79.422564   
29                                    Thorncliffe Park  43.705369 -79.349372   
30                            Richmond, Adelaide, King  43.650571 -79.384568   
31                        Dufferin, Dovercourt Village  43.669005 -79.442259   
33                        Fairview, Henry Farm, Oriole  43.778517 -79.346556   
34                     Northwood Park, York University  43.767980 -79.487262   
35       East Toronto, Broadview North (Old East York)  43.685347 

In [106]:
# Cluster 4
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3]

Postal Code      Borough  \
0          M3A   North York   
5          M9A    Etobicoke   
8          M4B    East York   
10         M6B   North York   
16         M6C         York   
17         M9C    Etobicoke   
18         M1E  Scarborough   
21         M6E         York   
26         M1H  Scarborough   
27         M2H   North York   
28         M3H   North York   
32         M1J  Scarborough   
38         M1K  Scarborough   
40         M3K   North York   
44         M1L  Scarborough   
46         M3L   North York   
49         M6L   North York   
50         M9L   North York   
51         M1M  Scarborough   
53         M3M   North York   
60         M3N   North York   
63         M6N         York   
64         M9N         York   
70         M9P    Etobicoke   
71         M1R  Scarborough   
72         M2R   North York   
77         M9R    Etobicoke   
78         M1S  Scarborough   
82         M1T  Scarborough   
85         M1V  Scarborough   
89         M9V    Etobicoke   
90         M1W  Scarborough   
93         M8W    Etobicoke   

                                        Neighbourhood   Latitude  Longitude  \
0                                           Parkwoods  43.753259 -79.329656   
5             Islington Avenue, Humber Valley Village  43.667856 -79.532242   
8                     Parkview Hill, Woodbine Gardens  43.706397 -79.309937   
10                                          Glencairn  43.709577 -79.445073   
16                                 Humewood-Cedarvale  43.693781 -79.428191   
17  Eringate, Bloordale Gardens, Old Burnhamthorpe...  43.643515 -79.577201   
18                  Guildwood, Morningside, West Hill  43.763573 -79.188711   
21                                Caledonia-Fairbanks  43.689026 -79.453512   
26                                          Cedarbrae  43.773136 -79.239476   
27                                  Hillcrest Village  43.803762 -79.363452   
28    Bathurst Manor, Wilson Heights, Downsview North  43.754328 -79.442259   
32                                Scarborough Village  43.744734 -79.239476   
38        Kennedy Park, Ionview, East Birchmount Park  43.727929 -79.262029   
40                                          Downsview  43.737473 -79.464763   
44                    Golden Mile, Clairlea, Oakridge  43.711112 -79.284577   
46                                          Downsview  43.739015 -79.506944   
49           North Park, Maple Leaf Park, Upwood Park  43.713756 -79.490074   
50                                      Humber Summit  43.756303 -79.565963   
51    Cliffside, Cliffcrest, Scarborough Village West  43.716316 -79.239476   
53                                          Downsview  43.728496 -79.495697   
60                                          Downsview  43.761631 -79.520999   
63                      Runnymede, The Junction North  43.673185 -79.487262   
64                                             Weston  43.706876 -79.518188   
70                                          Westmount  43.696319 -79.532242   
71                                  Wexford, Maryvale  43.750072 -79.295849   
72                        Willowdale, Willowdale West  43.782736 -79.442259   
77  Kingsview Village, St. Phillips, Martin Grove ...  43.688905 -79.554724   
78                                          Agincourt  43.794200 -79.262029   
82            Clarks Corners, Tam O'Shanter, Sullivan  43.781638 -79.304302   
85  Milliken, Agincourt North, Steeles East, L'Amo...  43.815252 -79.284577   
89  South Steeles, Silverstone, Humbergate, Jamest...  43.739416 -79.588437   
90                      Steeles West, L'Amoreaux West  43.799525 -79.318389   
93                             Alderwood, Long Branch  43.602414 -79.543484   

    Cluster Labels 1st Most Common Venue      2nd Most Common Venue  \
0                3                  Park          Convenience Store   
5                3              Pharmacy                       Bank   
8                3           Pizza Place       G

In [107]:
# Cluster 5
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4]

Postal Code     Borough  \
45          M2L  North York   
101         M8Y   Etobicoke   

                                         Neighbourhood   Latitude  Longitude  \
45                            York Mills, Silver Hills  43.757490 -79.374714   
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
45                4                  Park                  Pool   
101               4                  Park        Ice Cream Shop   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
45                    Zoo                 Field           Escape Room   
101    Italian Restaurant              Bus Stop         Shopping Mall   

           6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
45          Ethiopian Restaurant           Event Space    Falafel Restaurant   
101  Eastern European Restaurant  Gym / Fitness Center         Design Studio   

    9th Most Common Venue 10th Most Common Venue  
45                   Farm         Farmers Market  
101          Dessert Shop            Event Space